In [2]:
import matplotlib.pyplot as plt 
import numpy as np 
from scipy.spatial import Voronoi, voronoi_plot_2d
import math as m
import my_functions as mf
from tqdm import tqdm

### Interaction Force *Generates the movement of the cells (Steady state)*

In [3]:
# Initial conditions
S = 1
beta = 5
dt = 0.5
t_start = 0
t_end = 200
n_points = 100

screen_size = (-20, 20)

points = mf.gen_points(n_points, R = 20)
#points = mf.generate_spiral_points(n_points, 0.01, 1/6)


In [4]:
def interaction_force(point1, point2, beta = 5, S = 1):
    """Generates the interaction force and splits up into carteisan coordinates

    Returns:
        list: the components of the force in (F_x, F_y)
    """
    dist = m.dist(point1, point2)
    r_vec = (point1 - point2)/dist
    force = np.exp(-dist) - (S/beta)*np.exp(-dist/beta)
    
    force_x, force_y = force * r_vec
    return np.array([force_x, force_y])

def get_cell_forces(points, beta=5, S=1):
    """
    Returns:
        list of list: Returns a combined nested list where first element is all the forces components on the first cell.
        Each sublist is composed of (F_x, F_y) 
    """
    forces = []                         # All forces for all points
    for i, point1 in enumerate(points):
        cell_forces = []                # The forces for each cell
        for j, point2 in enumerate(points):
            if i != j:                  # Not counting the interaction of the cell on itself (even though its zero)
                force = interaction_force(point1, point2, beta, S)
                cell_forces.append(force)
        
        # The idea is that we sum all the x_components together to form one interaction force
        force_on_cell = np.sum(cell_forces, axis=0)     # [sum(x_1, x_2, ..., x_n) and sum(y_1, y_2, ..., y_n)]
        forces.append(force_on_cell)
    return np.array(forces)


def eulersim(t_start, t_end, dt, points, beta=5, S=1):
    
    # Obtaining initial vals
    list_of_points = [points]
    t_list = [t_start]
    
    while t_start < t_end:
        # Calculate new forces
        forces = get_cell_forces(points, beta, S)

        # Update all locations
        new_points = points + forces * dt
        points = new_points        
        
        # Update time step
        t_start += dt
        
        # Update lists
        list_of_points.append(points)  
        t_list.append(t_start)  
    
    return t_list, list_of_points

time, All_points = eulersim(t_start, t_end, dt, points, beta, S)

mf.get_steady_state(All_points) # This is a function that saves the system when steady state is reached

### *Simulating the cell size*
Vi benytter her at ved ligevægt rør cellevæggen hinanden så vores ligevægtsradius hedder:
$$
r_{ij}^* = \frac{\beta ln(\beta/S)}{\beta-1}
$$

In [5]:
r_cell = mf.get_cell_radius(beta, S)

### *Animating the cell movement*

In [6]:
import matplotlib.animation as animation
from IPython.display import HTML

fig, axis = plt.subplots()

def get_data(i):
    """Function for generating the data in the animation"""
    points = All_points[i]
    t = time[i]
    return points, t

def update(i):
    """
    Update function is what is happening every frame. Imagine that you have to make a new plot every frame,
    but instead you clear the background and overlay something else.
    """
    # Step 1 # Generate data
    points, t = get_data(i)

    # Step 2 # Clear previous plot and plot the updated plot
    axis.clear()          # Alternatively ax.clear() Clears the entire thing, but collections offers selection
    for i, point in enumerate(points):
        circle = plt.Circle((point[0], point[1]), r_cell, color = "blue", alpha = 0.2)
        axis.add_patch(circle)
        axis.scatter(point[0], point[1], marker=".", s = 8, color = "orange")

    # Step 3 # Modification of axis layout should occur in here
    axis.axis("equal")
    axis.set_xlim(screen_size)
    axis.set_ylim(screen_size)
    return None


anim = animation.FuncAnimation(fig, update, frames=150, interval=100) # Controls the plotted animation
plt.rcParams['animation.embed_limit'] = 2**128          # Limits the Bytes allocated to the animation
anim.save('Cell_movement4.gif', writer='Pillow', fps=15)      # Controls the animation for the downloadable gif and saves it
plt.close(fig)

HTML(anim.to_jshtml())      # Converts anim to an actual gif

MovieWriter Pillow unavailable; using Pillow instead.
